In [2]:
import os
import pandas as pd
import numpy as np
import sys
sys.path.append('../../Scripts')
from preprocess_daily import DailyPreprocessor
from generate_signals import SignalGenerator

In [3]:
self = DailyPreprocessor()
self.load_data()
self.make_match1()
self.make_match2()
self.make_match3()
self.make_match4()
self.make_match5()
self.make_match6()

1. 데이터를 로드합니다.
1-1. 네트워크가 로드되었습니다.
1-2. 테이블들이 로드되었습니다.
1-3. 네트워크의 모든 clean state requirement들을 체크했습니다.
1-4. 테이블들의 무결성 검사를 완료했습니다.
1-5. 주요 객체 (리스트, 딕셔너리)들을 저장했습니다.


In [4]:
self.match6

inter_no  phase_no ring_type  move_no inc_dire out_dire inc_angle  \
0         175         1         A        8        남        북       179   
1         175         1         B        4        북        남       001   
2         175         2         A        7        북        동       001   
3         175         2         B        3        남        서       179   
4         175         3         A        6        동        서       090   
..        ...       ...       ...      ...      ...      ...       ...   
103       210         2         B        2        서        동       270   
104       210         3         A        7        북        동       000   
105       210         3         B        4        북        남       000   
106       210         4         A        8        남        북       180   
107       210         4         B        3        남        서       180   

    out_angle    inc_edge_id   out_edge_id node_id turn_type  
0         000  -571542797_02  571500487_01      i0  straight  
1         180  -571500487_01  571542797_02      i0  straight  
2         090  -571500487_01  571545870_01      i0      left  
3         270  -571542797_02  571510153_01      i0      left  
4         270   571545870_02  571510153_01      i0  straight  
..        ...            ...           ...     ...       ...  
103       090            NaN           NaN     u60  straight  
104       090            NaN           NaN     u60      left  
105       180            NaN           NaN     u60  straight  
106       000            NaN           NaN     u60  straight  
107       270            NaN           NaN     u60      left  

[108 rows x 12 columns]

In [10]:
self.match6[self.match6.node_id==parent_id].dropna(subset=['inc_edge_id', 'out_edge_id'])

inter_no  phase_no ring_type  move_no inc_dire out_dire inc_angle  \
80       202         1         A        6        동        서       090   
81       202         1         B        2        서        동       270   

   out_angle   inc_edge_id      out_edge_id node_id turn_type  
80       270  571510152_02    -571510152_01      i9  straight  
81       090  571510152_01  571510152_01.65      i9  straight

In [13]:
self.match7 = self.match6.copy()
self.match7 = self.match7[['inter_no', 'node_id', 'move_no', 'inc_angle', 'out_angle', 'inc_dire', 'out_dire', 'inc_edge_id', 'out_edge_id']]
# parent_id = self.parent_ids[1]

for parent_id in self.parent_ids:
    m7 = self.match7[self.match7.node_id==parent_id].dropna(subset=['inc_edge_id', 'out_edge_id'])
    m6 = self.match6[self.match6.node_id==parent_id].dropna(subset=['inc_edge_id', 'out_edge_id'])
    inc_angles = [int(angle) for angle in np.unique(m7.inc_angle.values)]
    out_angles = [int(angle) for angle in np.unique(m7.out_angle.values)]
    # print(parent_id)
    # display(m6)
    # display(m7)
    # print(inc_angles)
    # print(out_angles)

In [14]:
# (1) 가능한 (진입방향, 진출방향) 목록 
flows = self.nema.dropna().apply(lambda row: (row['inc_dire'], row['out_dire']), axis=1).tolist()
# (2) 각 교차로별 방향 목록 : pdires (possible directions)
pdires = {}
for node_id in self.parent_ids:
    dires = self.match7[self.match7.node_id == node_id][['inc_dire','out_dire']].values.flatten()
    dires = {dire for dire in dires if type(dire)==str}
    pdires[node_id] = dires
# (3) 각 (교차로, 진입방향) 별 진입id 목록 : inc2id (incoming direction to incoming edge_id)
inc2id = {}
for node_id in self.parent_ids:
    for inc_dire in pdires[node_id]:
        df = self.match7[(self.match7.node_id==node_id) & (self.match7.inc_dire==inc_dire)]
        inc2id[(node_id, inc_dire)] = df.inc_edge_id.iloc[0]
# (4) 각 (교차로, 진출방향) 별 진출id 목록 : out2id (outgoing direction to outgoing edge_id)
out2id = {}
for node_id in self.parent_ids:
    for out_dire in pdires[node_id]:
        df = self.match7[(self.match7.node_id==node_id) & (self.match7.out_dire==out_dire)]
        out2id[(node_id, out_dire)] = df.out_edge_id.iloc[0]
# (5) 각 교차로별 가능한 (진입방향, 진출방향) 목록 : pflow (possible flows)
pflow = {}
for node_id in self.parent_ids:
    pflow[node_id] = [flow for flow in flows if set(flow).issubset(pdires[node_id])]

In [51]:
p2am = dict() # parent id to a list of aligned movement numbers
for parent_id in self.parent_ids:
    pnema = self.nema[self.nema.inc_dire.isin(pdires[parent_id]) & self.nema.out_dire.isin(pdires[parent_id])]
    p2am[parent_id] = list(pnema.move_no)

dire2vec = dict() # direction to unit vector
theta = np.pi/2
for dire in self.dires:
    dire2vec[dire] = np.array([np.cos(theta), np.sin(theta)])
    theta -= np.pi/4

plain_move_nos = list(range(1,17)) # plain movement numbers

p2pm2inc_edge_id = dict() # parent id to pm2inc_edge_id
p2pm2out_edge_id = dict() # parent id to pm2out_edge_id
for parent_id in self.parent_ids:
    pm2inc_edge_id = dict() # plain movement to incoming edge id
    pm2out_edge_id = dict() # plain movement to outgoing edge id
    for pm in plain_move_nos:
        row = self.nema[self.nema.move_no==pm].iloc[0]
        inc_dire = row.inc_dire
        out_dire = row.out_dire
        inc_vec_true = dire2vec[inc_dire]
        out_vec_true = dire2vec[out_dire]

        node = self.net.getNode(parent_id)
        # 교차로의 모든 (from / to) edges
        inc_edges = [edge for edge in node.getIncoming() if edge.getFunction() == ''] # incoming edges
        out_edges = [edge for edge in node.getOutgoing() if edge.getFunction() == ''] # outgoing edges
        # 교차로의 모든 (from / to) unit vector
        inc_vecs = []
        for inc_edge in inc_edges:
            start = inc_edge.getShape()[-1]
            end = inc_edge.getShape()[-2]
            inc_vec = np.array(end) - np.array(start)
            inc_vec = inc_vec / (inc_vec ** 2).sum() ** 0.5
            inc_vecs.append(inc_vec)
        out_vecs = []
        for out_edge in out_edges:
            start = out_edge.getShape()[0]
            end = out_edge.getShape()[1]
            out_vec = np.array(end) - np.array(start)
            out_vec = out_vec / (out_vec ** 2).sum() ** 0.5
            out_vecs.append(out_vec)
        # 매칭 엣지 반환
        inc_index = np.array([np.dot(inc_vec, inc_vec_true) for inc_vec in inc_vecs]).argmax()
        out_index = np.array([np.dot(out_vec, out_vec_true) for out_vec in out_vecs]).argmax()
        inc_edge_id = inc_edges[inc_index].getID()
        out_edge_id = out_edges[out_index].getID()
        pm2inc_edge_id[pm] = inc_edge_id
        pm2out_edge_id[pm] = out_edge_id
    p2pm2inc_edge_id[parent_id] = pm2inc_edge_id
    p2pm2out_edge_id[parent_id] = pm2out_edge_id

parent_id = self.parent_ids[0]
print(parent_id)
display(p2pm2inc_edge_id[parent_id])
display(p2pm2out_edge_id[parent_id])

i0


{1: '571545870_02',
 2: '571510153_02',
 3: '-571542797_02',
 4: '-571500487_01',
 5: '571510153_02',
 6: '571545870_02',
 7: '-571500487_01',
 8: '-571542797_02',
 9: '-571500487_01',
 10: '571510153_02',
 11: '571545870_02',
 12: '-571500487_01',
 13: '571510153_02',
 14: '-571500487_01',
 15: '-571500487_01',
 16: '571545870_02'}

{1: '571542797_02',
 2: '571545870_01',
 3: '571510153_01',
 4: '571542797_02',
 5: '571500487_01',
 6: '571510153_01',
 7: '571545870_01',
 8: '571500487_01',
 9: '571545870_01',
 10: '571500487_01',
 11: '571510153_01',
 12: '571545870_01',
 13: '571500487_01',
 14: '571510153_01',
 15: '571500487_01',
 16: '571500487_01'}

In [40]:
plain_move_nos = list(range(1,17)) # plain movement numbers
p2pm2inc_edge_id = dict() # parent id to pm2inc_edge_id
p2pm2out_edge_id = dict() # parent id to pm2out_edge_id
for parent_id in self.parent_ids:
    pm2inc_angle = dict()
    for pm in plain_move_nos:
        row = self.nema[self.nema.move_no==pm].iloc[0]
        # inc_dire = row.
# plain movement number(1-16) to (inc_angle, out_angle)


In [18]:
print(flows)
print(pdires)
print(inc2id)
print(out2id)
print(pflow)

[('동', '남'), ('서', '동'), ('남', '서'), ('북', '남'), ('서', '북'), ('동', '서'), ('북', '동'), ('남', '북'), ('북동', '남동'), ('남서', '북동'), ('남동', '남서'), ('북서', '남동'), ('남서', '북서'), ('북동', '남서'), ('북서', '북동'), ('남동', '북서')]
{'i0': {'북', '남', '동', '서'}, 'i1': {'북', '남', '서'}, 'i2': {'북', '남'}, 'i3': {'북', '남', '동', '서'}, 'i6': {'북', '남', '동', '서'}, 'i7': {'북', '남'}, 'i8': {'북', '남', '서', '동'}, 'i9': {'동', '서'}}
{('i0', '북'): '-571500487_01', ('i0', '남'): '-571542797_02', ('i0', '동'): '571545870_02', ('i0', '서'): '571510153_02', ('i1', '북'): '571542797_02.99', ('i1', '남'): '-571542810_01', ('i1', '서'): '571543469_02', ('i2', '북'): '571542811_02', ('i2', '남'): '-571542809_01', ('i3', '북'): '571556450_02', ('i3', '남'): '571540304_02', ('i3', '동'): '-571500475_01', ('i3', '서'): '571540303_02.21', ('i6', '북'): '571511538_02.121', ('i6', '남'): '571500585_02', ('i6', '동'): '-571542115_01', ('i6', '서'): '571500535_02.18', ('i7', '북'): '571542073_01', ('i7', '남'): '-571511538_02', ('i8', '북'): '571500583_01', 

In [ ]:

# (6) 가능한 이동류에 대하여 진입id, 진출id 배정 : matching
dires_right = ['북', '북서', '서', '남서', '남', '남동', '동', '북동'] # ex (북, 서), (서, 남) 등은 우회전 flow
self.matching = []
for node_id in self.parent_ids:
    inter_no = self.node2inter[node_id]
    # 좌회전과 직진(1 ~ 16)
    for (inc_dire, out_dire) in pflow[node_id]:
        move_no = self.nema[(self.nema.inc_dire==inc_dire) & (self.nema.out_dire==out_dire)].move_no.iloc[0]
        inc_edge_id = inc2id[(node_id, inc_dire)]
        out_edge_id = out2id[(node_id, out_dire)]
        new_row = pd.DataFrame({'inter_no':[inter_no], 'move_no':[move_no],
                                'inc_dire':[inc_dire], 'out_dire':[out_dire],
                                'inc_edge_id':[inc_edge_id], 'out_edge_id':[out_edge_id], 'node_id':[node_id]})
        self.matching.append(new_row)
    # 보행신호(17), 전적색(18)
    new_row = pd.DataFrame({'inter_no':[inter_no] * 2, 'move_no':[17, 18],
                            'inc_dire':[None]*2, 'out_dire':[None]*2,
                            'inc_edge_id':[None]*2, 'out_edge_id':[None]*2, 'node_id':[node_id]*2})
    self.matching.append(new_row)
    # 신호우회전(21)
    for d in range(len(dires_right)):
        inc_dire = dires_right[d]
        out_dire = dires_right[(d+2)%8]
        if {inc_dire, out_dire}.issubset(pdires[node_id]):
            inc_edge_id = inc2id[(node_id, inc_dire)]
            out_edge_id = out2id[(node_id, out_dire)]
            new_row = pd.DataFrame({'inter_no':[inter_no], 'move_no':[21],
                                    'inc_dire':[inc_dire], 'out_dire':[out_dire],
                                    'inc_edge_id':[inc_edge_id], 'out_edge_id':[out_edge_id], 'node_id':[node_id]})
            self.matching.append(new_row)
self.matching.append(self.match7[self.match7.node_id.isin(self.child_ids)])
self.matching = pd.concat(self.matching)
self.matching = self.matching.dropna(subset=['inc_edge_id', 'out_edge_id'])\
                .sort_values(by=['inter_no', 'node_id', 'move_no']).reset_index(drop=True)
self.matching['move_no'] = self.matching['move_no'].astype(int)
